#                                                 Transfer Learning Using Inception V3 (Pytorch)

Inception V3 is a little bit different Model from others, in a sense that it take the inpit 299 x 299, also it returns its own output type InceptionOutputs. So we need to check during tranining and inference.


## Extrcting files from folders

In [1]:
import zipfile
zip_files = ["/kaggle/input/dogs-vs-cats/test1.zip", "/kaggle/input/dogs-vs-cats/train.zip"]

for i in zip_files:
    with zipfile.ZipFile(i, 'r') as zip_ref:
        zip_ref.extractall("dogs-vs-cats/")

## Organize the images folder
I use two methods to create a dataloader


In [2]:
import os
import shutil

# Define the directory containing your images
source_dir = '/kaggle/working/dogs-vs-cats/train'  # Change this to your directory
cat_dir = 'kaggle/working/dogs-vs-cats/train/cat'  # Change this to your cat folder
dog_dir = 'kaggle/working/dogs-vs-cats/train/dog'  # Change this to your dog folder

# Create the cat and dog directories if they don't exist
os.makedirs(cat_dir, exist_ok=True)
os.makedirs(dog_dir, exist_ok=True)

# Loop through all files in the source directory
for filename in os.listdir(source_dir):
    if 'cat' in filename.lower():
        shutil.move(os.path.join(source_dir, filename), os.path.join(cat_dir, filename))
    elif 'dog' in filename.lower():
        shutil.move(os.path.join(source_dir, filename), os.path.join(dog_dir, filename))

print("Images have been organized into cat and dog folders.")

Images have been organized into cat and dog folders.


In [3]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/working'):
    print(dirname)
#     for filename in filenames:
#         print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/working
/kaggle/working/.virtual_documents
/kaggle/working/kaggle
/kaggle/working/kaggle/working
/kaggle/working/kaggle/working/dogs-vs-cats
/kaggle/working/kaggle/working/dogs-vs-cats/train
/kaggle/working/kaggle/working/dogs-vs-cats/train/dog
/kaggle/working/kaggle/working/dogs-vs-cats/train/cat
/kaggle/working/dogs-vs-cats
/kaggle/working/dogs-vs-cats/train
/kaggle/working/dogs-vs-cats/test1


In [4]:
%matplotlib inline
%config InlineBackend.figure_format = 'retina'

import matplotlib.pyplot as plt
from collections import OrderedDict
import torch
import time
from torch import nn
from torch import optim
import torch.nn.functional as F
from torchvision import datasets, transforms, models
from torch.utils.data import random_split
from torchvision.models.inception import InceptionOutputs
from huggingface_hub import PyTorchModelHubMixin


In [19]:
data_dir = '/kaggle/working/kaggle/working/dogs-vs-cats/'
test_dir = '/kaggle/working/dogs-vs-cats/test1'


train_transforms = transforms.Compose(
    [
        transforms.Resize(299),  # Ensure that images are resized to 299x299
        transforms.CenterCrop(299),  # Center crop to 299x299
        transforms.RandomRotation(45),
        transforms.GaussianBlur(3),
        transforms.RandomHorizontalFlip(),
        transforms.ToTensor()    
    ]
)


# Pass transforms in here
train_data = datasets.ImageFolder(data_dir + 'train', transform=train_transforms)

# Define the train-validation split ratio
train_size = int(0.8 * len(train_data))  # 80% for training
val_size = len(train_data) - train_size   # 20% for validation

# Split the dataset
train_dataset, val_dataset = random_split(train_data, [train_size, val_size])

# Create DataLoaders for train and validation sets
trainloader = torch.utils.data.DataLoader(train_dataset, batch_size=64, shuffle=True)
valloader = torch.utils.data.DataLoader(val_dataset, batch_size=64)

In [20]:
# Load model
model = models.inception_v3(pretrained=True)
model

Inception3(
  (Conv2d_1a_3x3): BasicConv2d(
    (conv): Conv2d(3, 32, kernel_size=(3, 3), stride=(2, 2), bias=False)
    (bn): BatchNorm2d(32, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
  )
  (Conv2d_2a_3x3): BasicConv2d(
    (conv): Conv2d(32, 32, kernel_size=(3, 3), stride=(1, 1), bias=False)
    (bn): BatchNorm2d(32, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
  )
  (Conv2d_2b_3x3): BasicConv2d(
    (conv): Conv2d(32, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
    (bn): BatchNorm2d(64, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
  )
  (maxpool1): MaxPool2d(kernel_size=3, stride=2, padding=0, dilation=1, ceil_mode=False)
  (Conv2d_3b_1x1): BasicConv2d(
    (conv): Conv2d(64, 80, kernel_size=(1, 1), stride=(1, 1), bias=False)
    (bn): BatchNorm2d(80, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
  )
  (Conv2d_4a_3x3): BasicConv2d(
    (conv): Conv2d(80, 192, kernel_size=(3, 3), stri

In [21]:
# Freeze parameters so we don't backprop through them
for param in model.parameters():
    param.requires_grad = False

### PyTorchModelHubMixin: To upload the model to huggingface repository. Cool feature to show case your models.
class Classifier(
    nn.Module,
    PyTorchModelHubMixin,
    repo_url="muneebable",
    pipeline_tag="image-classification",
    license="apache-2.0"
):
    def __init__(self):
        super().__init__()
        self.fc1 = nn.Linear(2048, 500)
        self.fc2 = nn.Linear(500, 2)
        self.dropout = nn.Dropout(p=0.2)
        self.output =  nn.LogSoftmax(dim=1)
    
    def forward(self, x):
        x = F.relu(self.fc1(x))
        x = self.dropout(x)
        x = self.fc2(x)
        return self.output(x)


classifier = Classifier()
# Replace the last layer of model with out classifier.
model.fc = classifier

In [22]:
model

Inception3(
  (Conv2d_1a_3x3): BasicConv2d(
    (conv): Conv2d(3, 32, kernel_size=(3, 3), stride=(2, 2), bias=False)
    (bn): BatchNorm2d(32, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
  )
  (Conv2d_2a_3x3): BasicConv2d(
    (conv): Conv2d(32, 32, kernel_size=(3, 3), stride=(1, 1), bias=False)
    (bn): BatchNorm2d(32, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
  )
  (Conv2d_2b_3x3): BasicConv2d(
    (conv): Conv2d(32, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
    (bn): BatchNorm2d(64, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
  )
  (maxpool1): MaxPool2d(kernel_size=3, stride=2, padding=0, dilation=1, ceil_mode=False)
  (Conv2d_3b_1x1): BasicConv2d(
    (conv): Conv2d(64, 80, kernel_size=(1, 1), stride=(1, 1), bias=False)
    (bn): BatchNorm2d(80, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
  )
  (Conv2d_4a_3x3): BasicConv2d(
    (conv): Conv2d(80, 192, kernel_size=(3, 3), stri

In [27]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
print(device)

criterion = nn.NLLLoss()

# Only train the classifier parameters, feature parameters are frozen
optimizer = optim.Adam(model.fc.parameters(), lr=0.003)

model.to(device);

cuda:0


In [36]:
criterion = nn.NLLLoss()
epochs = 1
steps = 0
running_loss = 0
print_every = 5
for epoch in range(epochs):
    for inputs, labels in trainloader:
        steps += 1
        # Move input and label tensors to the default device
        inputs, labels = inputs.to(device), labels.to(device)
        
         # Forward pass
        model.train()  # Ensure the model is in training mode
        
        output = model.forward(inputs)
        # In training mode, InceptionV3 returns both logits and aux_logits
        if isinstance(output, InceptionOutputs):
            logps = output.logits
        else:
            logps = output  # Handle the case where the output is already a Tensor

        loss = criterion(logps, labels)
        
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        running_loss += loss.item()
        
        if steps % print_every == 0:
            test_loss = 0
            accuracy = 0
            model.eval()
            with torch.no_grad():
                for inputs, labels in valloader:
                    inputs, labels = inputs.to(device), labels.to(device)
                    output = model.forward(inputs)
                    # In eval mode, InceptionV3 only returns logits
                    if isinstance(output, InceptionOutputs):
                        logps = output.logits
                    else:
                        logps = output
        
                    batch_loss = criterion(logps, labels)
                    
                    test_loss += batch_loss.item()
                    
                    # Calculate accuracy
                    ps = torch.exp(logps)
                    top_p, top_class = ps.topk(1, dim=1)
                    equals = top_class == labels.view(*top_class.shape)
                    accuracy += torch.mean(equals.type(torch.FloatTensor)).item()
                    
            print(f"Epoch {epoch+1}/{epochs}.. "
                  f"Train loss: {running_loss/print_every:.3f}.. "
                  f"Test loss: {test_loss/len(valloader):.3f}.. "
                  f"Test accuracy: {accuracy/len(valloader):.3f}")
            running_loss = 0
            model.train()

Epoch 1/1.. Train loss: 0.240.. Test loss: 0.160.. Test accuracy: 0.955
Epoch 1/1.. Train loss: 0.189.. Test loss: 0.139.. Test accuracy: 0.948
Epoch 1/1.. Train loss: 0.160.. Test loss: 0.132.. Test accuracy: 0.949
Epoch 1/1.. Train loss: 0.160.. Test loss: 0.117.. Test accuracy: 0.953
Epoch 1/1.. Train loss: 0.241.. Test loss: 0.211.. Test accuracy: 0.914
Epoch 1/1.. Train loss: 0.205.. Test loss: 0.138.. Test accuracy: 0.943
Epoch 1/1.. Train loss: 0.244.. Test loss: 0.142.. Test accuracy: 0.946
Epoch 1/1.. Train loss: 0.203.. Test loss: 0.157.. Test accuracy: 0.934
Epoch 1/1.. Train loss: 0.163.. Test loss: 0.185.. Test accuracy: 0.927
Epoch 1/1.. Train loss: 0.200.. Test loss: 0.124.. Test accuracy: 0.951
Epoch 1/1.. Train loss: 0.133.. Test loss: 0.119.. Test accuracy: 0.956
Epoch 1/1.. Train loss: 0.165.. Test loss: 0.111.. Test accuracy: 0.961
Epoch 1/1.. Train loss: 0.167.. Test loss: 0.122.. Test accuracy: 0.952
Epoch 1/1.. Train loss: 0.234.. Test loss: 0.118.. Test accuracy

In [38]:
#Save the model
filename_pth = 'ckpt_inception_v3_catdog.pth'
torch.save(model.state_dict(), filename_pth)

In [40]:
# ## Copied
# class CatDogDataset(Dataset):
#     def __init__(self, file_list, dir, mode='train', transform = None):
#         self.file_list = file_list
#         self.dir = dir
#         self.mode= mode
#         self.transform = transform
#         if self.mode == 'train':
#             if 'dog' in self.file_list[0]:
#                 self.label = 1
#             else:
#                 self.label = 0
            
#     def __len__(self):
#         return len(self.file_list)
    
#     def __getitem__(self, idx):
#         img = Image.open(os.path.join(self.dir, self.file_list[idx]))
#         if self.transform:
#             img = self.transform(img)
#         if self.mode == 'train':
#             img = img.numpy()
#             return img.astype('float32'), self.label
#         else:
#             img = img.numpy()
#             return img.astype('float32'), self.file_list[idx]

# #Transform the test dataset
# test_transforms = transforms.Compose(
#     [
#         transforms.Resize(255),
#         transforms.CenterCrop(224),
#         transforms.ToTensor()    
#     ]
# )

# test_dir = '/kaggle/working/dogs-vs-cats/test1'
# test_files = os.listdir(test_dir)
# testset = CatDogDataset(test_files, test_dir, mode='test', transform = test_transforms)
# testloader = torch.utils.data.DataLoader(testset, batch_size = 64, shuffle=False, num_workers=4)

# model.eval()
# fn_list = []
# pred_list = []
# for x, fn in testloader:
#     with torch.no_grad():
#         x = x.to(device)
#         output = model(x)
#         pred = torch.argmax(output, dim=1)
#         fn_list += [n[:-4] for n in fn]
#         pred_list += [p.item() for p in pred]

# submission = pd.DataFrame({"id":fn_list, "label":pred_list})
# submission.to_csv('submission.csv', index=False)

In [42]:
from kaggle_secrets import UserSecretsClient
user_secrets = UserSecretsClient()
secret_value_0 = user_secrets.get_secret("hugging_face")

# model.save_pretrained("inception_v3_catdog")
# model.push_to_hub("muneebable/inception_v3_catdog",token=secret_value_0)

# Push the model to the Hugging Face Hub (Need to create a Repo)
from huggingface_hub import HfApi

api = HfApi()
api.upload_file(
    path_or_fileobj=filename_pth,
    path_in_repo=filename_pth,
    repo_id="muneebable/inception_v3_catdog",
    token=secret_value_0
)

ckpt_inception_v3_catdog.pth:   0%|          | 0.00/105M [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/muneebable/inception_v3_catdog/commit/3586c9bb351d3391ef1f62cb6d75fc30e7f9a041', commit_message='Upload ckpt_inception_v3_catdog.pth with huggingface_hub', commit_description='', oid='3586c9bb351d3391ef1f62cb6d75fc30e7f9a041', pr_url=None, pr_revision=None, pr_num=None)